In [1]:
import os
import re
import fitz 
import csv

filenames = os.listdir()
prefix = '公开发行证券的公司信息披露内容与格式准则第2号'

pdf = [f for f in filenames if f.startswith(prefix) and f.endswith('.pdf')]

year = [f[-12:-5] for f in pdf]

def getText(pdf):
    text = ''
    doc = fitz.open(pdf)
    for page in doc:
        text += page.getText()
    doc.close()
    return(text)

def getSubtext(pdf):
    text = getText(pdf)
    p1 = re.compile('第二章\s*年度报告正文(.*)第三章\s*年度报告摘要',
                    re.DOTALL)
    subtext = p1.search(text).group(0)
    return(subtext)

# 主要部分
def getTOC(pdf):
    subtext = getSubtext(pdf)
    p = re.compile('(?<=\\n)(第\w{1,2}节)\s+(.*)(?=\\n)')
    listOftuple = p.findall(subtext)
    return(listOftuple)

toc = [getTOC(f) for f in pdf]

def getTOC_content(pdf):
    subtext = getSubtext(pdf)
    p = re.compile('(?<=\\n)(第\w{1,2}节)\s+(.*)(?=\\n)')
    index = []
    for match in p.finditer(subtext):
        s = match.start()
        e = match.end()
        index.append((s,e))

    content = []
    for i in range(len(index)-1):
        s = index[i][1]
        e = index[i+1][0]
        content.append(subtext[s:e])
    last_start = index[-1][1]
    last_end = subtext.rfind('\n第三章')
    content.append(subtext[last_start:last_end])
    return((index,content))

list_of_content = [getTOC_content(f) for f in pdf]

def export_to_html(pdf,toc,content):
    f = open('homework3_output_template.html', encoding='utf-8')
    html = f.read()
    f.close()
    template = '<div><h3>%s</h3><p>%s</p ></div>'
    toc_list = [t[0]+' '+ t[1] for t in toc]
    div = [template % (t,c) for (t,c) in zip(toc_list, content)]
    div = ''.join(div)
    html = html % div
    f = open('homework3_%s.html' % pdf, 'w',encoding='utf-8')
    f.write(html)
    f.close()
    return()

content_list = [c[1] for c in list_of_content]
export_to_html(pdf[0], toc[0], content_list[0])

Deprecation: 'getText' removed from class 'Page' after v1.19.0 - use 'get_text'.


FileNotFoundError: [Errno 2] No such file or directory: 'homework3_output_template.html'